# <center>Implementing LDA in Python</center>

<center>Dr. W.J.B. Mattingly</center>

<center>Smithsonian Data Science Lab and United States Holocaust Memorial Museum</center>

<center>February 2021</center>

## Importing the Required Libraries

In [1]:
#https://www.machinelearningplus.com/nlp/topic-modeling-gensim-python/#1introduction
import pandas as pd
import numpy as np
import json
import glob

#Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

#spacy
import spacy
from nltk.corpus import stopwords

#vis
import pyLDAvis
import pyLDAvis.gensim_models

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

## Preparing the Data

In [2]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\mango\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [3]:
stopwords = stopwords.words("english")

In [4]:
print (stopwords)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [6]:
# data = load_data("data/ushmm_dn.json")["texts"]
data = pd.read_csv('Data/Response_Comments_Metrics.csv')
data = list(data.RESP_COMMENT)
# print (data[0][0:90])

In [7]:
data[0][0:90]

'Learning new experiences with animation and testing my strengths asa designer and animator'

In [ ]:
def lemmatization(texts, allowed_postags=["NOUN", "ADJ", "VERB", "ADV"]):
    nlp = spacy.load("en_core_web_sm", disable=["parser", "ner"])
    texts_out = []
    for text in texts:
        doc = nlp(text)
        new_text = []
        for token in doc:
            if token.pos_ in allowed_postags:
                new_text.append(token.lemma_)
        final = " ".join(new_text)
        texts_out.append(final)
    return (texts_out)


lemmatized_texts = lemmatization(data)
print (lemmatized_texts[0][0:90])

C:\Users\mango\anaconda3\lib\site-packages\spacy\util.py:837: UserWarning: [W095] Model 'en_core_web_sm' (3.4.0) was trained with spaCy v3.4 and may not be 100% compatible with the current version (3.3.1). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [ ]:
def gen_words(texts):
    final = []
    for text in texts:
        new = gensim.utils.simple_preprocess(text, deacc=True)
        final.append(new)
    return (final)

data_words = gen_words(lemmatized_texts)

print (data_words[0][0:20])

In [10]:
#BIGRAMS AND TRIGRAMS
bigram_phrases = gensim.models.Phrases(data_words, min_count=5, threshold=100)
trigram_phrases = gensim.models.Phrases(bigram_phrases[data_words], threshold=100)

bigram = gensim.models.phrases.Phraser(bigram_phrases)
trigram = gensim.models.phrases.Phraser(trigram_phrases)

def make_bigrams(texts):
    return([bigram[doc] for doc in texts])

def make_trigrams(texts):
    return ([trigram[bigram[doc]] for doc in texts])

data_bigrams = make_bigrams(data_words)
data_bigrams_trigrams = make_trigrams(data_bigrams)

print (data_bigrams_trigrams[0][0:20])

['learn', 'new', 'experience', 'animation', 'test', 'strength', 'asa', 'designer', 'animator']


In [11]:
#TF-IDF REMOVAL
from gensim.models import TfidfModel

id2word = corpora.Dictionary(data_bigrams_trigrams)

texts = data_bigrams_trigrams

corpus = [id2word.doc2bow(text) for text in texts]
# print (corpus[0][0:20])

tfidf = TfidfModel(corpus, id2word=id2word)

low_value = 0.03
words  = []
words_missing_in_tfidf = []
for i in range(0, len(corpus)):
    bow = corpus[i]
    low_value_words = [] #reinitialize to be safe. You can skip this.
    tfidf_ids = [id for id, value in tfidf[bow]]
    bow_ids = [id for id, value in bow]
    low_value_words = [id for id, value in tfidf[bow] if value < low_value]
    drops = low_value_words+words_missing_in_tfidf
    for item in drops:
        words.append(id2word[item])
    words_missing_in_tfidf = [id for id in bow_ids if id not in tfidf_ids] # The words with tf-idf socre 0 will be missing

    new_bow = [b for b in bow if b[0] not in low_value_words and b[0] not in words_missing_in_tfidf]
    corpus[i] = new_bow


In [12]:
# id2word = corpora.Dictionary(all_texts)

# corpus = []
# for text in data_words:
#     new = id2word.doc2bow(text)
#     corpus.append(new)

# print (corpus[0][0:20])

# word = id2word[[0][:1][0]]
# print (word)

In [13]:
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus[:-1],
                                           id2word=id2word,
                                           num_topics=10,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha="auto")


In [14]:
test_doc = corpus[-1]

vector = lda_model[test_doc]
print (vector)

def Sort(sub_li):
    sub_li.sort(key = lambda x: x[1])
    sub_li.reverse()
    return (sub_li)
new_vector = Sort(vector)
print (new_vector)

[(0, 0.09429054), (1, 0.09817904), (2, 0.055370737), (3, 0.22694865), (4, 0.14122745), (5, 0.03568427), (6, 0.08367516), (7, 0.100482345), (8, 0.017456938), (9, 0.1466849)]
[(3, 0.22694865), (9, 0.1466849), (4, 0.14122745), (7, 0.100482345), (1, 0.09817904), (0, 0.09429054), (6, 0.08367516), (2, 0.055370737), (5, 0.03568427), (8, 0.017456938)]


In [21]:
lda_model.save("models/20221003_lda.model")

In [22]:
new_model = gensim.models.ldamodel.LdaModel.load("models/20221003_lda.model")

## Vizualizing the Data

In [15]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model, corpus, id2word, mds="mmds", R=30)
# vis

C:\Users\mango\anaconda3\lib\site-packages\pyLDAvis\_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


In [16]:
vis

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3      0.015623  0.076562       1        1  20.486592
4      0.051164 -0.430826       2        1  16.581280
0     -0.378357 -0.140886       3        1  13.739771
9     -0.238303  0.401552       4        1  11.386681
7      0.351183 -0.332047       5        1   8.718737
1      0.415219 -0.042944       6        1   8.101632
6      0.100831  0.463319       7        1   7.191365
2     -0.258741 -0.405176       8        1   6.234306
5     -0.454896  0.142355       9        1   4.415810
8      0.396277  0.268090      10        1   3.143826, topic_info=            Term           Freq          Total Category  logprob  loglift
104      subject  145111.000000  145111.000000  Default  30.0000  30.0000
89       student   79997.000000   79997.000000  Default  29.0000  29.0000
22          more   88219.000000   88219.000000  Default  28.0000  28.0000
80          well   56491.000000   56491.000000  Default  27.0000  27.0000
37          very   91419.000000   91419.000000  Default  26.0000  26.0000
...          ...            ...            ...      ...      ...      ...
425   supervisor    2010.564282    2011.409856  Topic10  -4.6363   3.4593
0      animation    1994.654283    1995.499805  Topic10  -4.6442   3.4593
2924   framework    1895.053856    1895.899600  Topic10  -4.6954   3.4593
2132    interact    1870.264769    1871.110313  Topic10  -4.7086   3.4593
1530       aware    1764.024391    1764.869964  Topic10  -4.7671   3.4593

[330 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
825       8  0.999829   ability
148       5  0.999933      able
1606     10  0.999628  academic
570      10  0.999648    access
558       5  0.999900  activity
...     ...       ...       ...
1242      8  0.999878     world
432       8  0.999957     write
668       8  0.999834   writing
323       6  0.999889      year
6491      2  0.999951      zoom

[300 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 5, 1, 10, 8, 2, 7, 3, 6, 9])

# Questions other than 1053 and 1070 Responses only

In [56]:
# data = load_data("data/ushmm_dn.json")["texts"]
df_resp = pd.read_csv('Data/Response_Comments_Metrics.csv')
# data = data[data.RE
# data = list(data.RESP_COMMENT)
# print (data[0][0:90])

In [57]:
df_resp

RESP_ID  RESP_SURVEY_ID  RESP_Q_ID  RESP_POINTS  resp_len  \
0       13926609          164973       1053          NaN        90   
1       13926622          164973       3131          4.0       102   
2       13926628          164973       3707          3.0       132   
3       14109824          187612       1053          NaN       125   
4       13926629          164973       3708          4.0        46   
...          ...             ...        ...          ...       ...   
385703  22675055          350031       1070          NaN        22   
385704  22623374          343111       3131          2.0       907   
385705  22675154          350299       1053          NaN       170   
385706  22623378          343111       3709          2.0      1218   
385707  22623379          343111       3709          3.0       475   

        avg_word_len  max_word_len  word_count  \
0                6.0            11          13   
1                4.0            10          19   
2                5.0            13          22   
3                4.5            11          22   
4                4.5             9           8   
...              ...           ...         ...   
385703           6.5            12           3   
385704           5.0            18         147   
385705           5.0            12          27   
385706           5.0            14         203   
385707           4.5            12          83   

                                             RESP_COMMENT  
0       Learning new experiences with animation and te...  
1       I learned a lot of new techniques and had expe...  
2       Goals of immersion and data visualisation were...  
3       The interaction between each of my classmate. ...  
4          Came in everyday, very happy with group effort  
...                                                   ...  
385703                             No improvements needed  
385704  Due to recent changes in leadership at the sch...  
385705  I liked the tutorial sessions. My tutor was re...  
385706  Leena was a satisfactory tutor, who seemingly ...  
385707  James was a satisfactory tutor, and injected v...  

[385708 rows x 9 columns]

In [58]:
data = df_resp.loc[(df_resp.RESP_Q_ID!=1053) & (df_resp.RESP_Q_ID!=1070)]['RESP_COMMENT']

In [60]:
data_resp_id = df_resp.loc[(df_resp.RESP_Q_ID!=1053) & (df_resp.RESP_Q_ID!=1070)]['RESP_ID']

In [20]:
lemmatized_texts = lemmatization(data)
print (lemmatized_texts[0][0:90])

data_words = gen_words(lemmatized_texts)
print (data_words[0][0:20])

C:\Users\mango\anaconda3\lib\site-packages\spacy\util.py:837: UserWarning: [W095] Model 'en_core_web_sm' (3.4.0) was trained with spaCy v3.4 and may not be 100% compatible with the current version (3.3.1). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


learn lot new technique experience work new screen space great
['learn', 'lot', 'new', 'technique', 'experience', 'work', 'new', 'screen', 'space', 'great']


In [21]:
#BIGRAMS AND TRIGRAMS
bigram_phrases = gensim.models.Phrases(data_words, min_count=5, threshold=100)
trigram_phrases = gensim.models.Phrases(bigram_phrases[data_words], threshold=100)

bigram = gensim.models.phrases.Phraser(bigram_phrases)
trigram = gensim.models.phrases.Phraser(trigram_phrases)

def make_bigrams(texts):
    return([bigram[doc] for doc in texts])

def make_trigrams(texts):
    return ([trigram[bigram[doc]] for doc in texts])

data_bigrams = make_bigrams(data_words)
data_bigrams_trigrams = make_trigrams(data_bigrams)

print (data_bigrams_trigrams[0][0:20])

['learn', 'lot', 'new', 'technique', 'experience', 'work', 'new', 'screen', 'space', 'great']


In [22]:
#TF-IDF REMOVAL
from gensim.models import TfidfModel

id2word = corpora.Dictionary(data_bigrams_trigrams)

texts = data_bigrams_trigrams

corpus = [id2word.doc2bow(text) for text in texts]
# print (corpus[0][0:20])

tfidf = TfidfModel(corpus, id2word=id2word)

low_value = 0.03
words  = []
words_missing_in_tfidf = []
for i in range(0, len(corpus)):
    bow = corpus[i]
    low_value_words = [] #reinitialize to be safe. You can skip this.
    tfidf_ids = [id for id, value in tfidf[bow]]
    bow_ids = [id for id, value in bow]
    low_value_words = [id for id, value in tfidf[bow] if value < low_value]
    drops = low_value_words+words_missing_in_tfidf
    for item in drops:
        words.append(id2word[item])
    words_missing_in_tfidf = [id for id in bow_ids if id not in tfidf_ids] # The words with tf-idf socre 0 will be missing

    new_bow = [b for b in bow if b[0] not in low_value_words and b[0] not in words_missing_in_tfidf]
    corpus[i] = new_bow


In [23]:
type(data_bigrams_trigrams)

list

In [24]:
data_bigrams_trigrams

[['learn',
  'lot',
  'new',
  'technique',
  'experience',
  'work',
  'new',
  'screen',
  'space',
  'great'],
 ['goal',
  'immersion',
  'datum_visualisation',
  'achieve',
  'feel',
  'more',
  'focus',
  'put',
  'motion',
  'capture',
  'storytelle'],
 ['come', 'everyday', 'very', 'happy', 'group', 'effort'],
 ['intensive', 'overall', 'positive', 'experience'],
 ['very', 'intelligent', 'engage', 'feedback', 'group'],
 ['content', 'course', 'provide', 'adequacy', 'align', 'objective'],
 ['content', 'deliver', 'provide', 'great', 'deal', 'knowledge', 'learn'],
 ['extremely',
  'friendly',
  'come',
  'even',
  'non',
  'teaching',
  'day',
  'show',
  'commitment',
  'technical',
  'knowledge',
  'course',
  'need'],
 ['high', 'level', 'content', 'case', 'present', 'class', 'learn'],
 ['level',
  'content',
  'deliver',
  'very',
  'well',
  'present',
  'very',
  'engaging',
  'assist',
  'motivation',
  'learn'],
 ['experience',
  'gain',
  'animation',
  'software',
  'entirely

In [25]:
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus[:-1],
                                           id2word=id2word,
                                           num_topics=10,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha="auto")


In [26]:
test_doc = corpus[-1]

vector = lda_model[test_doc]
print (vector)

def Sort(sub_li):
    sub_li.sort(key = lambda x: x[1])
    sub_li.reverse()
    return (sub_li)
new_vector = Sort(vector)
print (new_vector)

[(0, 0.15399261), (1, 0.118609525), (2, 0.04983521), (3, 0.12212789), (4, 0.03810325), (5, 0.15043305), (6, 0.0621007), (7, 0.11237193), (8, 0.124662206), (9, 0.06776361)]
[(0, 0.15399261), (5, 0.15043305), (8, 0.124662206), (3, 0.12212789), (1, 0.118609525), (7, 0.11237193), (9, 0.06776361), (6, 0.0621007), (2, 0.04983521), (4, 0.03810325)]


In [53]:
# save non-1053-1070 model
lda_model.save("models/20221003_lda_non10531070.model")

## Vizualizing the Data

In [27]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model, corpus, id2word, mds="mmds", R=30)
vis

C:\Users\mango\anaconda3\lib\site-packages\pyLDAvis\_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
5      0.385840  0.262264       1        1  19.606208
3      0.121621  0.440997       2        1  14.088668
0     -0.342973 -0.252760       3        1  13.052926
7     -0.248558  0.428280       4        1  10.354010
1      0.206202 -0.436156       5        1   9.902057
8     -0.177680  0.156979       6        1   8.723296
9     -0.118438 -0.433019       7        1   8.544908
6     -0.483446  0.022010       8        1   5.602062
2      0.182221 -0.089384       9        1   5.084642
4      0.475212 -0.099209      10        1   5.041221, topic_info=               Term          Freq         Total Category  logprob  loglift
25             very  21034.000000  21034.000000  Default  30.0000  30.0000
85          subject  20487.000000  20487.000000  Default  29.0000  29.0000
30         feedback  14565.000000  14565.000000  Default  28.0000  28.0000
8              work  14011.000000  14011.000000  Default  27.0000  27.0000
66             time  11745.000000  11745.000000  Default  26.0000  26.0000
...             ...           ...           ...      ...      ...      ...
646           vague    496.319761    497.143658  Topic10  -4.7012   2.9859
900      suggestion    495.952836    496.776782  Topic10  -4.7020   2.9859
964      contribute    480.702502    481.526522  Topic10  -4.7332   2.9858
1993       document    466.946375    467.770501  Topic10  -4.7622   2.9858
971   unfortunately    458.948482    459.772669  Topic10  -4.7795   2.9857

[330 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
123       5  0.999717        able
726       7  0.998479       above
385       9  0.999043  absolutely
9         4  0.999329     achieve
501       4  0.998759    activity
...     ...       ...         ...
59        4  0.999913        well
407       2  0.998655     willing
8         7  0.999946        work
285      10  0.999040    workshop
427       8  0.999362        year

[300 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[6, 4, 1, 8, 2, 9, 10, 7, 3, 5])

## Checking model result

In [28]:
from gensim import corpora,models,similarities

index = similarities.SparseMatrixSimilarity(lda_model[corpus],num_features=len(id2word))

In [30]:
# t = np.random.randint(len(Xtest))
# query_document = re.split('\W+',Xtest[t].lower())
query_document = data_bigrams_trigrams[-1]

query_bow = id2word.doc2bow(query_document)
sims = index[lda_model[query_bow]]
docNumber = sorted(enumerate(sims), key=lambda x: x[1], reverse=True)[0][0]
docNumber
# print('Predicted:',y_names[ytrain[docNumber]])
# print('Ground Truth:',y_names[ytest[t]])

77220

In [31]:
query_document

['satisfactory',
 'tutor',
 'inject',
 'valuable',
 'insight',
 'industry',
 'experience',
 'studio',
 'most',
 'time',
 'helpful',
 'provide',
 'good',
 'feedback',
 'min',
 'week',
 'however',
 'external',
 'tutor',
 'only',
 'present',
 'class',
 'week',
 'reduce',
 'time',
 'able',
 'dedicate',
 'studio',
 'also',
 'wish',
 'able',
 'bring',
 'more',
 'industry',
 'specialist',
 'studio',
 'perhaps',
 'create',
 'more',
 'diverse',
 'discussion',
 'studio',
 'space']

In [40]:
topic_id = sorted(lda_model[query_bow], key=lambda x: x[1], reverse=True)[0][0]

In [41]:
topic_id

0

In [63]:
type(data_resp_id)

pandas.core.series.Series

In [ ]:
def getTopicByRespId( query_resp_id, data_resp_id, data_bigrams_trigrams, lda_model):
    doc_posn = data_resp_id[data_resp_id==query_resp_id]
    doc_id = np.where(data_resp_id.to_numpy()==query_resp_id)[0][0]
    query_document = data_bigrams_trigrams[doc_id]

    query_bow = id2word.doc2bow(query_document)
    topic_id = sorted(lda_model[query_bow], key=lambda x: x[1], reverse=True)[0][0]
    print(topic_id, doc_posn, query_document)
    print(data[doc_posn.index.tolist()[0]])
    return(topic_id)
    
for i in data_resp_id:
    query_resp_id = i
    o_topic = getTopicByRespId(query_resp_id = query_resp_id
                     ,data_resp_id = data_resp_id
                     ,data_bigrams_trigrams = data_bigrams_trigrams
                     ,lda_model = lda_model)
    print(query_resp_id, o_topic)

5 1    13926622
Name: RESP_ID, dtype: int64 ['learn', 'lot', 'new', 'technique', 'experience', 'work', 'new', 'screen', 'space', 'great']
I learned a lot of new techniques and had experience working with a new screen space, which was great.
13926622 5
5 2    13926628
Name: RESP_ID, dtype: int64 ['goal', 'immersion', 'datum_visualisation', 'achieve', 'feel', 'more', 'focus', 'put', 'motion', 'capture', 'storytelle']
Goals of immersion and data visualisation were achieved, where I felt more focus could be put on motion capture, VR and storytelling
13926628 5
3 4    13926629
Name: RESP_ID, dtype: int64 ['come', 'everyday', 'very', 'happy', 'group', 'effort']
Came in everyday, very happy with group effort
13926629 3
5 5    13926630
Name: RESP_ID, dtype: int64 ['intensive', 'overall', 'positive', 'experience']
It was intensive but it was an overall positive experience
13926630 5
5 7    13926631
Name: RESP_ID, dtype: int64 ['very', 'intelligent', 'engage', 'feedback', 'group']
Very intellige

In [191]:
np.where(data_resp_id.to_numpy()==13926631)[0][0]

4

In [200]:
data_resp_id

1         13926622
2         13926628
4         13926629
5         13926630
7         13926631
            ...   
385685    22623225
385686    22623226
385704    22623374
385706    22623378
385707    22623379
Name: RESP_ID, Length: 77221, dtype: int64

In [125]:
data

1         I learned a lot of new techniques and had expe...
2         Goals of immersion and data visualisation were...
4            Came in everyday, very happy with group effort
5         It was intensive but it was an overall positiv...
7         Very intelligent and engages with feedback and...
                                ...                        
385685    never is all my life of education have i had s...
385686    shit teacher. contradicts himself often. has a...
385704    Due to recent changes in leadership at the sch...
385706    Leena was a satisfactory tutor, who seemingly ...
385707    James was a satisfactory tutor, and injected v...
Name: RESP_COMMENT, Length: 77221, dtype: object